## Failover 2 Gateways

Im vorherigen Post wurde die Konfiguration von 2 IP-Adressen beschrieben die beide mit dem Internet verbunden sind. Meist ist dabei aber der Sinn das man bei einem Ausfall der Verbindung auf die andere umschalten kann. Dies ist durch setzten der Default Route ohne weiteres möglich.

Sapnnend wird es jedoch wenn diese Umschaltung automatisch erfolgt!
<!-- TEASER_END -->

Selbes Scenario wie im Post vorher:

![Failover](http://b9i.de/failover.svg)

### Manuelle Umschaltung:

dazu gibt es 2 mögliche Befehle:

#### klassisch via `route`

    route del default
    route add default gw $Gateway1

#### via Iproute2

`ip route replace default via $Gateway1 dev eth1`

dabei wird die alte Route geloescht und die neue gleich eingetragen. Diese Kommando ist atomar, dh. es wird komplett ausgeführt. Oder gar nicht. Sehr praktisch wenn die Umschaltung Remote erfolgt. Im *klassischen* Fall kann es wenn keine Vorkehrungen getroffen werden, bzw. das Netz nicht komplett sauber, wie im ersten Post beschrieben wurde, konfiguriert wurde, dass man dann keinen Zugriff mehr auf die Maschine hat.

## automatische Umschaltung

z.B. via Monit <http://mmonit.com/monit/>, dies ist ein kleines Überwachungstool. Es ist nicht so mächtig wie Nagios oder check_mk, aber für diesen Zweck viel besser geeignet weil es schneller aufgesetzt und erheblich weniger Resourcen verbraucht.

### Installation monit

einfach der Anleitung auf der Homepage folgen. Alle Beschreibungen und Beispiele gehen von einem anderen Pfad aus! Bei Centos ist der Pfad zur Konfigdatei: `/etc/monit.conf`

### Überwachung der Internetverbindung
Eigentlich testet man immer einen Host im Internet der ziemlich sicher erreichbar ist. z.B. <http://web.de> dies würde in diesem Fall nicht zum gewünschten Ergebnis führen. 

* direkt den Gateway anbingen: 
** Vorteil: wenn die Verbindung wieder da ist kann wieder zurück geschalten werden.
** Nachteil: Unterbrechungen beim Provider werden nicht detektiert.

* Internet Host anpingen:
** Sollte eigentlich über beide Provider erreichbar sein** -> wenn der Link wieder online ist wird nicht gemerkt

mit folgender Eintrag im Konfigurationsfile von Monit kann dann umgeschalten werden:

    check host Gateway with address $Gateway1
        if failed icmp type echo count 3 with timeout 20 seconds then exec "/sbin/ip route replace default via $Gateway2 dev eth2"
        else if recovered then exec "/sbin/ip route replace default via $Gateway1 dev eth1"
        alert <email-adresse>
        

wieder muessen die Variablen $Gateway[12] durch echte Werte ersetzt werden. 